## Prepare

In [47]:
%load_ext autoreload
%autoreload 2
# add . to module name
import sys
sys.path.append('../src/')

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [48]:
from package.logger import setup
setup("INFO")

In [49]:
import os

import folium

from package import strtime
from package.osm import osm
from package.mcr5.h3 import (
    plot_h3_cells_on_folium,
)
from package.mcr5.labels import read_labels_for_nodes
from package.logger import Timed, rlog
from package import storage
from package.geometa import GeoMeta
from package.mcr.data import NetworkType, OSMData

In [50]:
geo_meta_path = "../data/geometa.pkl"
city_id = "Koeln"
stops = "../data/cleaned/stops.csv"
structs = "../data/structs.pkl"

geo_meta = GeoMeta.load(geo_meta_path)
geo_data = OSMData(
	geo_meta,
	city_id,
	additional_network_types=[NetworkType.DRIVING],
)
nodes = geo_data.osm_nodes
edges = geo_data.osm_edges
driving_nodes, _, _ = geo_data.additional_networks[NetworkType.DRIVING]

[19:05:41] INFO     Using existing OSM data                                                              ]8;id=480549;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/osm/osm.py\osm.py]8;;\:]8;id=926742;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/osm/osm.py#106\106]8;;\

           INFO     Loading OSM network from cache (walking)                                              ]8;id=149453;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/osm/osm.py\osm.py]8;;\:]8;id=160433;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/osm/osm.py#69\69]8;;\

[19:05:46] INFO     Using existing OSM data                                                              ]8;id=133991;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/osm/osm.py\osm.py]8;;\:]8;id=615742;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/osm/osm.py#106\106]8;;\

           INFO     Loading OSM network from cache (driving)                                              ]8;id=555678;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/osm/osm.py\osm.py]8;;\:]8;id=195396;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/osm/osm.py#69\69]8;;\

## Fetch POIs

In [51]:
import matplotlib.pyplot as plt
from package.minute_city import minute_city

In [52]:
pois = minute_city.fetch_pois_for_area(geo_meta.boundary, nodes)
pois.head(3)

name         id         lat        lon  \
0       Weinhaus Linke  444820559  50.9543812  6.9189388   
1  O'Donnell Moonshine  448400534  50.9382394  6.9408967   
2         Hopfenrausch  751978797  50.9493105  6.9237323   

                   geometry     type  nearest_osm_node_id   distance  
0  POINT (6.91894 50.95438)  grocery           3890235659  13.327476  
1  POINT (6.94090 50.93824)  grocery           6513219752  16.685454  
2  POINT (6.92373 50.94931)  grocery           1888001367   9.187973

## Visualize POIs

In [53]:
def rgb2hex(rgb):
	return "#{:02x}{:02x}{:02x}".format(int(rgb[0] * 255), int(rgb[1] * 255), int(rgb[2] * 255))
types = pois["type"].unique()

types = ['grocery', 'education', 'health', 'banks', 'parks', 'sustenance', 'shops']

# Get a colormap and create a color mapping
colormap = plt.colormaps.get_cmap('tab10')
color_mapping = {type_: rgb2hex(colormap(i)) for i, type_ in enumerate(types)}
color_mapping

bbox = nodes.unary_union.convex_hull.bounds

m = folium.Map(location=[50.9375, 6.9603], zoom_start=12)
geo_meta.add_to_folium_map(m)
for _, poi in pois.iterrows():
	folium.CircleMarker(
		location=(poi.lat, poi.lon),
		popup=poi["name"],
		radius=1,
		color=color_mapping[poi["type"]]
	).add_to(m)

m

## Calculate 15-minute-city metric

In [54]:
mcr5_output_path = "../data/mcr5/Koeln"

In [55]:
labels_per_scenario = {}
for entry in os.scandir(mcr5_output_path):
    if not entry.is_dir():
        continue

    labels = read_labels_for_nodes(
        entry.path, pois.nearest_osm_node_id.unique()
    )

    labels = minute_city.add_pois_to_labels(labels, pois)
    labels_per_scenario[entry.name] = labels


In [61]:
labels_per_scenario["car"].head(3)

target_id_osm   time  cost  n_transfers human_readable_time  \
0       60220350  28856    19            1            08:00:56   
1      218016627  28846    19            1            08:00:46   
2      218016627  28871     0            1            08:01:11   

      start_id_hex  nearest_osm_node_id  grocery  education  health  banks  \
0  891fa198357ffff             60220350        0          1       0      0   
1  891fa198357ffff            218016627        0          0       0      0   
2  891fa198317ffff            218016627        0          0       0      0   

   parks  sustenance  shops  
0      0           0      0  
1      0           1      0  
2      0           1      0

In [62]:
types = list(pois["type"].unique())

In [79]:
profiles_df_per_scenario = {}
for scenario, labels in labels_per_scenario.items():
	profiles_df_per_scenario[scenario] = minute_city.get_profiles_df(labels, types)

[19:13:49] INFO     Grouping labels                                                               ]8;id=973008;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py\minute_city.py]8;;\:]8;id=936572;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py#73\73]8;;\

           INFO     Grouping labels done (0.01 seconds)                                           ]8;id=131018;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py\minute_city.py]8;;\:]8;id=494384;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py#73\73]8;;\

           INFO     Calculating profiles                                                          ]8;id=297203;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py\minute_city.py]8;;\:]8;id=275097;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py#81\81]8;;\

  0%|          | 0/10 [00:00<?, ?it/s]

[19:13:50] INFO     Calculating profiles done (0.36 seconds)                                      ]8;id=802429;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py\minute_city.py]8;;\:]8;id=537948;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py#81\81]8;;\

...

           INFO     Calculating profiles                                                          ]8;id=460140;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py\minute_city.py]8;;\:]8;id=151784;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py#81\81]8;;\

  0%|          | 0/10 [00:00<?, ?it/s]

           INFO     Calculating profiles done (0.34 seconds)                                      ]8;id=522250;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py\minute_city.py]8;;\:]8;id=818151;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py#81\81]8;;\

           INFO     Creating profiles dataframe                                                   ]8;id=649664;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py\minute_city.py]8;;\:]8;id=170849;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py#92\92]8;;\

           INFO     Creating profiles dataframe done (0.02 seconds)                               ]8;id=270754;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py\minute_city.py]8;;\:]8;id=17013;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py#92\92]8;;\

In [87]:
m = folium.Map(location=[50.9375, 6.9603], zoom_start=12)
plot_h3_cells_on_folium(
    profiles_df_per_scenario["public_transport"]["cost_0"].to_dict(),
    m,
    color="red",
    popup_callback=lambda x: strtime.seconds_to_str_time(int(x)),
)
m


In [ ]:
m = folium.Map(location=[50.9375, 6.9603], zoom_start=12)
plot_h3_cells_on_folium(
    (profiles_df_per_scenario["car"]["required_cost_for_optimal"]).to_dict(),
    m,
    color="blue",
    popup_callback=lambda x: f"cost: {x/100:.2f}€",
)
m